# Residual Model

In [100]:
import torch
import torch.nn as nn
import pickle
import numpy as np
import faiss

NUM_HIDDEN_NODES = 1536
NUM_HIDDEN_LAYERS = 1
DROPOUT_RATE = 0.1
CURRENT_DEVICE = "cuda:3"
REVERSE_RANKER_PATH = "/datadrive/ruohan/fix_residual_overfit/reverse_alpha0.5_layer1_residual1000_100_1000_0.0001_768.model"
PASSAGE_NP_PATH = "/home/jianx/results/passage_0__emb_p__data_obj_0.pb"
PASSAGE_MAP_PATH = "/datadrive/jianx/data/annoy/100_ance_passage_map.dict"
QUERY_TRAIN_NP_PATH = "/home/jianx/results/query_0__emb_p__data_obj_0.pb"
QUERY_TEST_NP_PATH = "/home/jianx/results/test_query_0__emb_p__data_obj_0.pb"
QUERY_MAP_PATH = "/datadrive/jianx/data/annoy/100_ance_query_train_map.dict"
TRUE_PATH = "/datadrive/jianx/data/results/all_search_rankings_100_100_flat.csv"
TRAIN_RANK_PATH = "/datadrive/jianx/data/train_data/ance_testing_rank100_nqueries50000_20000_Sep_03_22:56:31.csv"
QUERY_DEV_NP_PATH = "/home/jianx/results/dev_query_0__emb_p__data_obj_0.pb"

In [101]:
# Define the network
class ResidualNet(torch.nn.Module):

    def __init__(self, embed_size):
        super(ResidualNet, self).__init__()
        
        self.input = nn.Linear(embed_size, NUM_HIDDEN_NODES)
        self.relu = nn.ReLU()
        self.normlayer = nn.LayerNorm(NUM_HIDDEN_NODES)
        self.dropout = nn.Dropout(p=DROPOUT_RATE)
        self.output = nn.Linear(NUM_HIDDEN_NODES, embed_size)

    def forward(self, x):
        identity = x
        out = x
        for i in range(NUM_HIDDEN_LAYERS):
            out = self.input(out)
            out = self.relu(out)
            out = self.normlayer(out)
            out = self.dropout(out)
            out = self.output(out)
            out += identity
#             out = self.relu(out)
        return out

    def parameter_count(self):
        return sum(p.numel() for p in self.parameters() if p.requires_grad)

In [102]:
def obj_reader(path):
    with open(path, 'rb') as handle:
        return pickle.load(handle, encoding="bytes")
def obj_writer(obj, path):
    with open(path, 'wb') as handle:
        pickle.dump(obj, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [103]:
# Load ground truth ranking
def load_true_dict(k = 100, path = TRUE_PATH):
    true_dict = {}
    with open(path, "r") as file:
        for line in file:
            qid = int(line.split(",")[0])
            pid = int(line.split(",")[1])
            rank = int(line.split(",")[2])
            if rank > k:
                continue
            if pid not in true_dict.keys():
                true_dict[pid] = {}
            true_dict[pid][qid] = rank
    return true_dict
def load_forward_dict(k = 100, path = TRUE_PATH):
    true_dict = {}
    with open(path, "r") as file:
        for line in file:
            qid = int(line.split(",")[0])
            pid = int(line.split(",")[1])
            rank = int(line.split(",")[2])
            if rank > k:
                continue
            if qid not in true_dict.keys():
                true_dict[qid] = {}
            true_dict[qid][pid] = rank
    return true_dict

In [104]:
def load_forward_dict_rerank(rerank_dict, k = 100, path = TRUE_PATH):
    true_dict = {}
    with open(path, "r") as file:
        for line in file:
            qid = int(line.split(",")[0])
            pid = int(line.split(",")[1])
            tempqids = rerank_dict.get(pid,{})
            rank = tempqids.get(qid,0)
            if rank > k:
                continue
            if pid not in true_dict.keys():
                true_dict[pid] = {}
            true_dict[pid][qid] = rank
    return true_dict

In [105]:
def transform_np_transformation(query_np, b=500):
    n = int(query_np.shape[0]/b) + 1

    corpus_output = []
    for i in range(n):
        start = i * b
        end = (i + 1) * b
        if i == n-1:
            end = query_np.shape[0]
        q_embed = query_np[start:end,:]
        q_embed = torch.from_numpy(q_embed).to(CURRENT_DEVICE)
        corpus_output.append(reverse_ranker(q_embed).detach().cpu().numpy())
    corpus_np = np.concatenate(corpus_output[:-1])
    corpus_np = np.concatenate((corpus_np, corpus_output[-1]))
    print(corpus_np.shape)
    return corpus_np

In [106]:
# 6. Find n nearest queries of a passage
# 7. Compare with the groud truth
def evaluate_reverse_ranker(pred_rank, true_rank, k = 100):
    top_true = []
    top_pred = []
    for pid, qids in pred_rank.items():
        n_top_true = len(true_rank.get(pid, {}))
        temp_pred = np.fromiter(qids.values(), dtype=int)
        n_top_pred = sum((temp_pred != 0) & (temp_pred <= k))
        top_true.append(n_top_true)
        top_pred.append(n_top_pred)
    return top_true, top_pred

def generate_pred_rank(query_index, true_dict, baseline_dict, passage_embed, 
                       qid_mapping, pid_reverse_mapping, n=100, k=100):
    pid_list = list(baseline_dict.keys())
    p_embed_list = []
    all_results = {}
    print("Begin append.")
    for i, pid in enumerate(pid_list):
        if i >= n:
            break
        pid_r = pid_reverse_mapping[pid]
        p_embed = np.array(passage_embed[pid_r])
        p_embed_list.append(p_embed)
    p_embed_all = np.stack(p_embed_list)
    print("Finish append.")
    print("Begin search.")
    _, near_qids = query_index.search(p_embed_all, k)
    print("Finish search.")
    for i, pid in enumerate(pid_list):
        temp_results = {}
        for qid in near_qids[i]:
            qid = qid_mapping[qid]
            try:
                rank = true_dict[pid][qid]
            except:
                rank = 0
            temp_results[qid] = rank
        all_results[pid] = temp_results
    return all_results

N_PASSAGE = 100
TRAIN_PASSAGE = 200000
def load_train(path, N_PASSAGE = 100, TRAIN_PASSAGE = 200000):
    with open(path) as file:
        my_dict = {}
        count = 0
        for line in file:
            count += 1
            if count <= TRAIN_PASSAGE * 100:
                continue            
            if count > (TRAIN_PASSAGE + N_PASSAGE) * 100:
                break
            tokens = line.split(",")
            pid = int(tokens[0])
            qid = int(tokens[1])
            rank = int(tokens[2].rstrip())
            if pid not in my_dict:
                my_dict[pid] = {}
            my_dict[pid][qid] = rank
    return my_dict

def compare_with_baseline(query_index, true_dict_100, forward_baseline_rank, passage_embed, 
                          qid_mapping, pid_reverse_mapping,n):
    pred_rank = generate_pred_rank(query_index, true_dict_100, forward_baseline_rank, 
                                   passage_embed, qid_mapping, pid_reverse_mapping, n=n)
    top_true, top_pred = evaluate_reverse_ranker(pred_rank, true_dict_100, k = 100)
    print("New model: {}".format(np.mean(top_pred)/np.mean(top_true)))
    top_true_baseline, top_pred_baseline = evaluate_reverse_ranker(forward_baseline_rank, true_dict_100, k = 100)
    print("Baseline model: {}".format(np.mean(top_pred_baseline)/np.mean(top_true_baseline)))
    return top_true, top_pred, top_true_baseline, top_pred_baseline, pred_rank

In [107]:
def delete_zeros(myDict):
    out_dict = {key:val for key, val in myDict.items() if val != 0}
    return set(list(out_dict.keys()))

In [108]:
def compare_specific_passage(pred_rank_test1, forward_baseline_rank_test1, n):
    count = 0
    count_loss = 0
    all_count = 0
    all_count_loss = 0
    for i in range(n):
        pid = list(pred_rank_test1.keys())[i]
        pred = delete_zeros(pred_rank_test1[pid])
        baseline = delete_zeros(forward_baseline_rank_test1[pid])
        diff = pred - baseline
        if diff != set():
            count += 1
            all_count += len(diff)
#             print("Newly found {}".format(diff))
        diff_loss = baseline - pred
        if diff_loss != set():
            count_loss += 1
            all_count_loss += len(diff_loss)
#             print("Lose {}".format(diff_loss))
    print("Percentage of passages with newly found exposing queries: {}".format(count/n))
    print("Percentage of passages that lose originaly found exposing queries: {}".format(count_loss/n))
    print("Number of newly found exposing queries:{} Number of lost exposing queries:{} Net gain:{}".format(all_count, all_count_loss, all_count - all_count_loss))

In [109]:
def add_test_queries_residual(q_np, test_q_np, transform):
    if transform:
        new_test_q_np = transform_np_transformation(test_q_np)
    else:
        new_test_q_np = test_q_np
    new_q_np = np.concatenate((q_np, new_test_q_np))
    out_index = generate_index(new_q_np)
    original_q = q_np.shape[0]
    new_q = new_q_np.shape[0]
    count = 0
    mapping = {}
    for i in range(original_q, new_q):
        mapping[count] = i
        count += 1
    return out_index, mapping
def generate_ground_truth(out_index, test_np, qid_mapping, k=100):
    _, near_pids = out_index.search(test_np, k)
    results = {}
    for i in range(test_np.shape[0]):
        qid = qid_mapping[i]
        for rank, pid in enumerate(near_pids[i,:]):
            if qid not in results.keys():
                results[qid] = {}
            results[qid][pid] = rank + 1
    return results
def generate_test_model_rank(results, p_np, qindex, n=10, k=100, b=40000):
    accuracies = []
    all_pids = []
    rank_results = {}
    print("Start appending")
    for qid, pids in results.items():
        pid_list = list(pids.keys())
        all_pids = all_pids + pid_list
    p_embed = p_np[all_pids,:]
    print("Start search")
    if p_embed.shape[0] <= b:
        _, all_near_qids = qindex.search(p_embed, n)
    else:
        N = int(p_embed.shape[0]/b) + 1
        outputs = []
        for i in range(N):
            print(i)
            start = i * b
            end = (i + 1) * b
            if i == N-1:
                end = p_embed.shape[0]
            temp_embed = p_embed[start:end,:]
            _, temp_qids = qindex.search(temp_embed, n)
            outputs.append(temp_qids)
        all_near_qids = np.concatenate(outputs[:-1])
        all_near_qids = np.concatenate((all_near_qids, outputs[-1]))
        print(all_near_qids.shape)
    print("End search")
    count = 1
    for qid, _ in results.items():
        near_qids = all_near_qids[(count - 1) * k:count * k,:]
        rank_results[qid] = near_qids
        match = sum(sum(near_qids == qid))
        print(match)
        accuracies.append(match/k)
        count += 1
    return accuracies, rank_results
def generate_lower_n(results, n, k=100):
    accuracies = []
    for qid, near_qids in results.items():
        lower_near_qids = near_qids[:,:n]
        match = sum(sum(lower_near_qids == qid))
        accuracies.append(match/k)
    return accuracies
def generate_index(obj_np):
    dim = obj_np.shape[1]
    out_index = faiss.IndexFlatIP(dim)
    out_index.add(obj_np)
    return out_index
def load_train_dict(path):
    with open(path, "r") as file:
        pos_dict = {}
        neg_dict = {}
        count = 0
        for line in file:
            tokens = line.split(",")
            pid = int(tokens[0])
            qid = int(tokens[1])
            rank = int(tokens[2].rstrip())
            if rank == 0:
                if pid not in neg_dict:
                    neg_dict[pid] = {}
                neg_dict[pid][qid] = 200
            else:
                if pid not in pos_dict:
                    pos_dict[pid] = {}
                pos_dict[pid][qid] = rank
    return pos_dict, neg_dict
def count_unique_queries(train_pos, train_neg):
    unique_queries = set()
    for pid, qids in train_pos.items():
        for qid, rank in qids.items():
            unique_queries.add(qid)
    for pid, qids in train_neg.items():
        for qid, rank in qids.items():
            unique_queries.add(qid)
    print(len(unique_queries))
    return unique_queries

In [110]:
def main_eval_residual(path, query_new_np):
    dev_query_index_split, query_dev_map_split = add_test_queries_residual(query_new_np, query_dev_np, True)
    dev_query_results_split = generate_ground_truth(passage_index, query_dev_np, query_dev_map_split)
    accuracies_dev_pred_100_split, results_dev_pred_100_split = generate_test_model_rank(dev_query_results_split, 
                                                                    passage_new_np, dev_query_index_split, n=100)
    accuracies_dev_pred_10_split = generate_lower_n(results_dev_pred_100_split, n=10)
    obj_writer({"ranking": dev_query_results_split, "mapping": query_dev_map_split, 
                "accuracies100pred": accuracies_dev_pred_100_split, "accuracies10pred": accuracies_dev_pred_10_split,
                "results100pred": results_dev_pred_100_split}, path + "dev_set.result")
    return accuracies_dev_pred_100_split, accuracies_dev_pred_10_split

In [8]:
checkpoint = torch.load(REVERSE_RANKER_PATH)
reverse_ranker = ResidualNet(embed_size=768)
reverse_ranker.load_state_dict(checkpoint['model'])
reverse_ranker.to(CURRENT_DEVICE)
reverse_ranker.eval()

ResidualNet(
  (input): Linear(in_features=768, out_features=1536, bias=True)
  (relu): ReLU()
  (normlayer): LayerNorm((1536,), eps=1e-05, elementwise_affine=True)
  (dropout): Dropout(p=0.1, inplace=False)
  (output): Linear(in_features=1536, out_features=768, bias=True)
)

In [9]:
print("Load passages.")
passage_np = obj_reader(PASSAGE_NP_PATH)
pid_mapping = obj_reader(PASSAGE_MAP_PATH)
print("Load queries.")
query_np = obj_reader(QUERY_TRAIN_NP_PATH)
qid_mapping = obj_reader(QUERY_MAP_PATH)
print("Load pre-processed results.")
true_dict_100 = load_true_dict(k=100)
pid_reverse_mapping = {v: k for k, v in pid_mapping.items()}

Load passages.
Load queries.
Load pre-processed results.


In [10]:
query_new_np = transform_np_transformation(query_np)
passage_new_np = transform_np_transformation(passage_np)

(502939, 768)
(8841823, 768)


In [20]:
query_dev_np = obj_reader(QUERY_DEV_NP_PATH)

In [11]:
# 5. Add the new numpy array to Flatindex
dim = query_new_np.shape[1]
query_index = faiss.IndexFlatIP(dim)
query_index.add(query_new_np)

In [24]:
passage_index = generate_index(passage_np)

In [111]:
forward_baseline_rank_test = load_train(TRAIN_RANK_PATH, N_PASSAGE = 20000, TRAIN_PASSAGE = 0)
top_true_test, top_pred_test, top_true_baseline_test, top_pred_baseline_test, pred_rank_test = compare_with_baseline(query_index, true_dict_100, forward_baseline_rank_test, passage_new_np, qid_mapping, pid_reverse_mapping, n=20000)
compare_specific_passage(pred_rank_test, forward_baseline_rank_test, n=20000)

Begin append.
Finish append.
Begin search.
Finish search.
New model: 0.9443781551170262
Baseline model: 0.8389811840293714
Percentage of passages with newly found exposing queries: 0.2646
Percentage of passages that lose originaly found exposing queries: 0.0514
Number of newly found exposing queries:13801 Number of lost exposing queries:2318 Net gain:11483


In [37]:
train_pos_dict, train_neg_dict = load_train_dict("/datadrive/jianx/data/train_data/ance_training_rank100_nqueries50000_200000_Sep_03_22:56:31.csv")
unique_queries = count_unique_queries(train_pos_dict, train_neg_dict)
print("{} queries have been seen by the reverse ranker during training.".format(len(unique_queries)))
expose = count_unique_queries(pred_rank_test, pred_rank_test)
expose_append = count_unique_queries(pred_rank_test, pred_rank_test)
print("{}/{} of the exposing queries have not seen by the reverse ranker while training.".format(len(expose_append
       - unique_queries), len(expose_append)))

49968
49968 queries have been seen by the reverse ranker during training.
417243
417243
374942/417243 of the exposing queries have not seen by the reverse ranker while training.


In [27]:
accuracies_dev_pred_100, accuracies_dev_pred_10 = main_eval_residual("/datadrive/ruohan/evaluation/best_residual_split_50000_morepos_fixoverfit/", query_new_np)

(6980, 768)
Start appending
Start search
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
(698000, 100)
End search
100
73
100
94
100
100
100
88
100
100
100
100
100
100
100
54
97
100
100
66
100
100
95
100
100
68
100
100
100
100
100
97
82
91
85
100
55
100
97
99
99
36
100
100
100
94
100
61
62
62
98
100
98
85
97
99
100
99
87
100
88
82
100
98
100
100
100
1
48
100
99
100
99
90
97
100
87
100
100
100
94
100
93
98
93
100
100
44
100
57
100
87
100
100
71
100
77
100
97
97
98
100
95
100
100
77
88
53
100
100
100
98
100
100
100
100
95
100
42
100
90
100
100
100
97
100
100
99
99
100
84
96
95
100
100
100
66
100
99
68
100
100
100
99
84
95
100
98
100
100
100
90
72
89
87
100
99
100
100
99
100
95
100
98
100
93
99
100
100
94
52
99
99
91
100
100
100
91
94
99
84
100
65
90
87
100
100
100
62
100
93
100
100
100
97
99
100
88
93
100
87
100
81
100
100
100
97
100
93
100
61
70
97
100
59
100
100
87
94
87
100
99
98
75
100
100
92
87
100
100
85
84
98
100
82
91
100
100
100
81
100
100
100
96
100
98
100
98
93
87
100
40
66
100
95


100
91
100
100
78
100
99
99
92
100
95
100
100
79
99
100
100
100
100
77
100
99
99
100
99
100
100
98
96
100
100
98
100
100
98
100
99
100
100
92
100
67
65
100
100
100
94
82
100
100
100
94
100
100
55
100
99
78
97
100
96
50
93
100
100
72
97
87
100
99
97
100
86
90
100
99
92
98
100
100
95
47
83
96
92
83
81
77
98
58
100
91
70
87
97
98
92
81
90
86
100
42
81
98
99
93
100
100
98
91
91
100
95
97
100
100
97
100
100
87
99
100
99
92
94
100
75
100
90
86
99
100
78
88
100
100
100
98
100
90
100
100
98
95
99
100
100
100
100
99
100
91
94
100
99
73
100
100
99
99
87
95
93
100
81
66
84
100
99
100
100
70
100
57
100
100
62
100
100
85
96
86
66
100
99
100
67
88
94
38
100
100
100
100
95
100
97
100
86
84
89
99
92
97
91
100
100
57
100
100
99
72
99
99
100
100
93
95
72
100
82
93
97
92
94
64
100
96
93
98
99
100
95
100
94
100
88
99
94
100
99
100
87
100
82
98
80
76
91
100
100
100
94
100
98
100
96
100
99
100
99
92
100
98
95
100
94
78
89
100
89
94
100
89
76
100
86
100
100
88
86
100
88
100
84
100
100
100
100
98
100
97
97
92

96
100
94
100
100
100
100
100
96
98
100
100
99
100
100
91
100
99
98
100
96
100
100
85
82
99
100
100
96
98
98
81
100
99
93
95
97
100
55
85
98
100
97
98
100
61
79
100
99
100
84
75
70
73
97
84
98
99
98
97
100
100
100
100
93
90
89
95
95
99
100
45
99
68
100
100
97
100
89
96
67
100
100
100
100
97
99
100
70
100
100
100
97
100
100
100
100
57
54
100
65
90
100
100
98
100
90
100
88
95
100
89
100
100
87
99
96
98
64
100
100
98
100
100
100
99
100
76
100
100
100
100
100
99
62
100
100
85
100
100
100
99
95
94
100
97
91
99
84
77
78
100
99
100
82
92
87
85
61
62
69
29
87
100
100
100
100
100
100
84
100
100
100
96
100
100
100
92
97
99
95
95
100
100
100
85
100
100
98
99
99
100
100
100
80
100
93
100
96
71
98
100
66
100
72
100
87
100
100
97
100
100
100
78
100
90
100
64
100
80
72
73
92
100
100
100
100
90
98
87
100
100
75
69
100
100
99
98
100
100
98
100
99
99
99
99
100
100
100
100
100
74
100
99
100
79
85
93
98
88
92
86
96
82
100
97
100
96
95
67
98
98
95
93
98
94
97
100
100
84
96
97
99
98
73
83
98
100
100
99
100


In [28]:
print("Reverse Ranker Average Accuracies (n=100): {}".format(np.mean(accuracies_dev_pred_100)))
print("Reverse Ranker Average Accuracies (n=10): {}".format(np.mean(accuracies_dev_pred_10)))

Reverse Ranker Average Accuracies (n=100): 0.9314770773638968
Reverse Ranker Average Accuracies (n=10): 0.5365687679083094


In [ ]:
RESULT_PATH = "/datadrive/ruohan/reverse_ranker/residual/train_query_50000_morepos_layer1_reludel/"
obj_writer(forward_baseline_rank_test, RESULT_PATH + "forward_baseline_rank_test.pickle")
obj_writer(top_true_baseline_test, RESULT_PATH + "top_true_test.pickle")
obj_writer(top_pred_test, RESULT_PATH + "top_pred_test.pickle")
obj_writer(top_true_baseline_test, RESULT_PATH + "top_true_baseline_test.pickle")
obj_writer(top_pred_baseline_test, RESULT_PATH + "top_pred_baseline_test.pickle")
obj_writer(pred_rank_test, RESULT_PATH + "pred_rank_test.pickle")

# Redundant

In [ ]:
true_rerank_dict_100 = load_true_dict(100, RERANK_TRUE_PATH)

In [113]:
forward_baseline_rank_test_rerank = load_train(TRAIN_RERANK_PATH, N_PASSAGE = 20000, TRAIN_PASSAGE = 0)
top_true_test_rerank, top_pred_test_rerank, top_true_baseline_test_rerank, top_pred_baseline_test_rerank, pred_rank_test_rerank = compare_with_baseline(query_index, true_rerank_dict_100, forward_baseline_rank_test_rerank, passage_new_np, qid_mapping, pid_reverse_mapping, n=20000)
compare_specific_passage(pred_rank_test_rerank, forward_baseline_rank_test_rerank, n=20000)

Begin append.
Finish append.
Begin search.
Finish search.
New model: 0.726410277831927
Baseline model: 0.6476649307972931
Percentage of passages with newly found exposing queries: 0.3708
Percentage of passages that lose originaly found exposing queries: 0.17745
Number of newly found exposing queries:13576 Number of lost exposing queries:5093 Net gain:8483


In [ ]:
RESULT_PATH = "/datadrive/ruohan/reverse_ranker/residual/train_query_50000_morepos_layer1_reludel/"
obj_writer(forward_baseline_rank_test_rerank, RESULT_PATH + "forward_baseline_rank_test.pickle")
obj_writer(top_true_baseline_test_rerank, RESULT_PATH + "top_true_test.pickle")
obj_writer(top_pred_test_rerank, RESULT_PATH + "top_pred_test.pickle")
obj_writer(top_true_baseline_test_rerank, RESULT_PATH + "top_true_baseline_test.pickle")
obj_writer(top_pred_baseline_test_rerank, RESULT_PATH + "top_pred_baseline_test.pickle")
obj_writer(pred_rank_test_rerank, RESULT_PATH + "pred_rank_test.pickle")

# Compare Reverse Results for Full-retrieval vs. Reranking

In [39]:
forward_dict_100 = load_forward_dict_rerank(true_rerank_dict_100, 100)
len(true_rerank_dict_100) - len(forward_dict_100)
top_true_baseline, top_pred_baseline = evaluate_reverse_ranker(forward_dict_100, true_rerank_dict_100, k = 100)
print("Baseline model: {}".format(np.mean(top_pred_baseline)/np.mean(top_true_baseline)))

In [56]:
def compare_full_rerank(full_dict, rerank_dict):
    count = 0
    for pid, qids in full_dict.items():
        count += len(set(qids) & set(rerank_dict.get(pid, [])))
    return count

In [59]:
count = compare_full_rerank(true_dict_100, true_rerank_dict_100)

In [63]:
count

16924247

# Generate training data for full query log

In [94]:
# Randomly select 200,000 passages for train, 20,000 passages for test
# Output their top 100 retrieval results to csv file
import random
TRAIN_SIZE = 200000
TEST_SIZE = 20000

random.seed(0)
pids = list(forward_dict_100.keys())
selected_pids = random.sample(range(len(pids)),TRAIN_SIZE + TEST_SIZE)
selected_pids = [pids[i] for i in selected_pids]
train_pids = selected_pids[:TRAIN_SIZE]
test_pids = selected_pids[TRAIN_SIZE:]
if len(train_pids) != TRAIN_SIZE or len(test_pids) != TEST_SIZE:
    print("Error occured in sampling process!")

In [98]:
def write_csv_data(pids, forward_dict, path):
    with open(path,'w') as f:
        for pid in pids:
            temp_dict = forward_dict[pid]
            for qid, rank in temp_dict.items():
                f.write('{},{},{}\n'.format(pid, qid, rank))

In [99]:
write_csv_data(train_pids, forward_dict_100, "/datadrive/ruohan/data/rerank_full_query_log_train.csv")

Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in f

Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in f

Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in f

Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in f

Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in f

...

Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in f

Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in f

Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in f

Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in f

Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in forward dict
Error in f

In [97]:
write_csv_data(test_pids, forward_dict_100, "/datadrive/ruohan/data/rerank_full_query_log_test.csv")